In [1]:
import vectorbt as vbt
import vectorbt.utils.datetime_ as dtutils
import pandas as pd
import pandas_ta as ta
import numpy as np
import warnings
import os
import datetime
import time
from binance.client import Client
from IPython.display import clear_output
warnings.filterwarnings('ignore')

from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error, mean_absolute_error, mean_absolute_percentage_error
from sklearn import linear_model
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score

In [139]:
start = '1 year ago'
interval = ['30m', '1m']
end = "now"
for intv in interval:
    data_path = './record' + '/' + start + ' - '+ intv + '.csv'
    data = vbt.BinanceData.download('BTCUSDT', start=start, end=end, interval=intv)
    df = data.get()
    df.index = df.index.tz_convert('Asia/Taipei')
    df.ta.cores=4
    df.to_csv(data_path)

0it [00:00, ?it/s]

0it [00:00, ?it/s]

In [140]:
# LogisticRegression
test_size = 0.3

intv = '30m'
start = '1 year ago'
df = pd.read_csv('./record' + '/' + start + ' - ' + intv + '.csv')
df = df[:-1]
train_df = pd.DataFrame([], columns = ['lastRF', 'shade_ratio', 'volume', 'dis_LHP', 'dis_LLP', 'RF'])
p_length = 20

for i in range(100, df.shape[0]):
    op = df['Open'].iat[i-1]
    cl = df['Close'].iat[i-1]
    hi = df['High'].iat[i-1]
    lo = df['Low'].iat[i-1]
    vo = df['Volume'].iat[i-1]
    LHP = max(df['High'][i-p_length:i])
    LLP = min(df['Low'][i-p_length:i])
    pre = []
    sign = 1 if cl > op else -1
    pre.append(cl - op)
    if sign == 1:
        if lo != op:
            shade_ratio = (hi - cl) / (op - lo)
        else:
            continue
    else:
        if lo != cl:
            shade_ratio = (hi - op) / (cl - lo)
        else:
            continue
    pre.append(shade_ratio)
    pre.append(vo)
    pre.append(LHP - hi)
    pre.append(lo - LLP)
    pre.append(1 if cl > op else 0)
    tmp = pd.DataFrame([pre], columns = ['lastRF', 'shade_ratio', 'volume', 'dis_LHP', 'dis_LLP', 'RF'])
    train_df = pd.concat([train_df, tmp])

train_df = train_df.reset_index(drop = True)
x = train_df.drop('RF', axis = 1)
y = train_df['RF']

sc_x = StandardScaler()
x = sc_x.fit_transform(x)
x = pd.DataFrame(x, columns = ['lastRF', 'shade_ratio', 'volume', 'dis_LHP', 'dis_LLP'])
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size = test_size, random_state = 40)
y_train = y_train.astype('int')
y_test = y_test.astype('int')

classifier = LogisticRegression(random_state = 0)
classifier.fit(x_train, y_train)
predictions = classifier.predict(x_test)
print ("Accuracy : ", accuracy_score(y_test, predictions))

Accuracy :  0.9955374466433837


Open      High       Low     Close     Volume  \
Open time                                                                      
2022-07-22 10:35:00+08:00  23090.68  23096.47  23044.93  23074.16  184.37756   
2022-07-22 10:40:00+08:00  23073.12  23082.08  23047.51  23059.53  148.38984   
2022-07-22 10:45:00+08:00  23059.53  23089.00  23024.95  23037.26  253.77401   
2022-07-22 10:50:00+08:00  23039.55  23075.75  23032.38  23073.93  190.35233   
2022-07-22 10:55:00+08:00  23073.92  23074.89  22962.45  22987.42  442.25448   
...                             ...       ...       ...       ...        ...   
2022-10-22 10:10:00+08:00  19157.98  19164.54  19157.35  19160.28  232.76100   
2022-10-22 10:15:00+08:00  19159.82  19164.39  19159.20  19161.23  182.21922   
2022-10-22 10:20:00+08:00  19161.44  19162.00  19155.38  19159.06  286.54609   
2022-10-22 10:25:00+08:00  19159.06  19160.41  19155.02  19158.54  281.19033   
2022-10-22 10:30:00+08:00  19158.54  19162.64  19157.75  19162.11  100.82927   

                                                Close time  Quote volume  \
Open time                                                                  
2022-07-22 10:35:00+08:00 2022-07-22 02:39:59.999000+00:00  4.254404e+06   
2022-07-22 10:40:00+08:00 2022-07-22 02:44:59.999000+00:00  3.422038e+06   
2022-07-22 10:45:00+08:00 2022-07-22 02:49:59.999000+00:00  5.852202e+06   
2022-07-22 10:50:00+08:00 2022-07-22 02:54:59.999000+00:00  4.389512e+06   
2022-07-22 10:55:00+08:00 2022-07-22 02:59:59.999000+00:00  1.017711e+07   
...                                                    ...           ...   
2022-10-22 10:10:00+08:00 2022-10-22 02:14:59.999000+00:00  4.459969e+06   
2022-10-22 10:15:00+08:00 2022-10-22 02:19:59.999000+00:00  3.491667e+06   
2022-10-22 10:20:00+08:00 2022-10-22 02:24:59.999000+00:00  5.489765e+06   
2022-10-22 10:25:00+08:00 2022-10-22 02:29:59.999000+00:00  5.387057e+06   
2022-10-22 10:30:00+08:00 2022-10-22 02:34:59.999000+00:00  1.931970e+06   

                           Number of trades  Taker base volume  \
Open time                                                        
2022-07-22 10:35:00+08:00              7816           80.48490   
2022-07-22 10:40:00+08:00              7054           73.03311   
2022-07-22 10:45:00+08:00             10103          115.43495   
2022-07-22 10:50:00+08:00              8221           96.06778   
2022-07-22 10:55:00+08:00             13833          193.92139   
...                                     ...                ...   
2022-10-22 10:10:00+08:00              8846          113.26464   
2022-10-22 10:15:00+08:00              8280          103.22252   
2022-10-22 10:20:00+08:00              9224          131.89739   
2022-10-22 10:25:00+08:00              8286          135.38048   
2022-10-22 10:30:00+08:00              2942           68.90393   

                           Taker quote volume  
Open time                                      
2022-07-22 10:35:00+08:00        1.857087e+06  
2022-07-22 10:40:00+08:00        1.684254e+06  
2022-07-22 10:45:00+08:00        2.662233e+06  
2022-07-22 10:50:00+08:00        2.215319e+06  
2022-07-22 10:55:00+08:00        4.461497e+06  
...                                       ...  
2022-10-22 10:10:00+08:00        2.170291e+06  
2022-10-22 10:15:00+08:00        1.977947e+06  
2022-10-22 10:20:00+08:00        2.526982e+06  
2022-10-22 10:25:00+08:00        2.593663e+06  
2022-10-22 10:30:00+08:00        1.320268e+06  

[26496 rows x 10 columns]

In [93]:
def custom_indicator_30m(open_time, open_price, high_price, low_price, close_price, volume):
    global classifier, p_length, sc_x
    length = open_price.shape[0]
    entries = np.zeros(length, dtype = bool)
    
    for i in range(p_length + 1, length-1):
        lastRF = close_price[i-1] - open_price[i-1]
        shade_ratio = 0.0
        if lastRF > 0:
            if open_price[i-1] == low_price[i-1]:
                continue
            else:
                shade_ratio = (high_price[i-1] - close_price[i-1]) / (open_price[i-1] - low_price[i-1])
        else:
            if close_price[i-1] == low_price[i-1]:
                continue
            else:
                shade_ratio = (high_price[i-1] - open_price[i-1]) / (close_price[i-1] - low_price[i-1])
        LHP = max(high_price[i-p_length:i])
        LLP = min(low_price[i-p_length:i])
        vol = volume[i]
        to_pred = [lastRF, shade_ratio, vol, LHP - high_price[i-1], low_price[i-1] - LLP]
        to_pred = pd.DataFrame([to_pred], columns = ['lastRF', 'shade_ratio', 'volume', 'dis_LHP', 'dis_LLP'])
        to_pred = sc_x.transform(to_pred)
        to_pred = pd.DataFrame(to_pred, columns = ['lastRF', 'shade_ratio', 'volume', 'dis_LHP', 'dis_LLP'])
        entries[i] = classifier.predict(to_pred)[0]
        
    return entries

In [104]:
def custom_indicator_1m(open_time, open_price, high_price, low_price, close_price, volume):
    global sl_per, tp_per, move_tp, move_sl, entries_30m
    length = open_price.shape[0]
    entries = np.zeros(length, dtype=bool)
    exits = np.zeros(length, dtype=bool)
    SL_out = np.zeros(length, dtype=float)
    TP_out = np.zeros(length, dtype=float)
    
    idx_30m = 0
    cnt_30m = 0
    in_market = 0
    SL_price = 0.0
    protect = 0
    TP = 0.0
    OP_price = 0.0
    for i in range(length-1):
        cnt_30m += 1
        if cnt_30m == 30:
            cnt_30m = 0
            idx_30m += 1
            if idx_30m >= len(entries_30m):
                break
            if in_market == 0 and entries_30m[idx_30m]:
                in_market = 1
                entries[i] = True
                SL_price = open_price[i] * (1 - sl_per * 0.01)
                TP = tp_per
                OP_price = open_price[i]
                protect = 0
                continue
            if in_market == 1 and not(entries_30m[idx_30m]):
                in_market = 0
                exits[i] = True
        
        if in_market == 1:
            TP_price = OP_price * (1 + TP * 0.01)
            if close_price[i] >= TP_price:
                protect += 1
                if protect == 1:
                    SL_price = OP_price
                else:
                    SL_price += OP_price * move_sl * 0.01
                TP += move_tp
            elif close_price[i] <= SL_price:
                in_market = 0
                exits[i] = True
                
            SL_out[i] = SL_price
            TP_out[i] = OP_price * (1 + TP * 0.01)
    
    return entries, exits, SL_out, TP_out

In [141]:
start = '1 year ago'
df = pd.read_csv('./record' + '/' + start + ' - 30m.csv')
df = df[:-1]
df_1m = pd.read_csv('./record' + '/' + start + ' - 1m.csv')
df_1m = df_1m[:-1]

sl_per = 0.2
tp_per = 0.1
move_tp = 0.04
move_sl = 0.02
debug = False

ind = vbt.IndicatorFactory(
    class_name = 'Custom',
    short_name = 'cus',
    input_names = ['open_time', 'open_price', 'high_price', 'low_price', 'close_price', 'volume'],
    param_names = [],
    output_names = ['entries']
).from_apply_func(custom_indicator_30m)

res = ind.run(df['Open time'], df['Open'], df['High'], df['Low'], df['Close'], df['Volume'])
entries_30m = res.entries

ind2 = vbt.IndicatorFactory(
    class_name = 'open_in_1m',
    short_name = 'open_1m',
    input_names = ['open_time', 'open_price', 'high_price', 'low_price', 'close_price', 'volume'],
    param_names = [],
    output_names = ['entries', 'exits', 'SL_out', 'TP_out']
).from_apply_func(custom_indicator_1m)

res_1m = ind2.run(df_1m['Open time'], df_1m['Open'], df_1m['High'], df_1m['Low'], df_1m['Close'], df_1m['Volume'])

In [142]:
size = np.full(df_1m['Open'].shape[0], 100.0, dtype=float)

pf = vbt.Portfolio.from_signals(
    close = df_1m['Close'],
    entries = res_1m.entries,
    exits = res_1m.exits,
    init_cash = 1000.0,
    size_type = 'Value',
    size = size
)

pf.stats()

Start                              0.000000
End                           525598.000000
Period                        525599.000000
Start Value                     1000.000000
End Value                       2315.758318
Total Return [%]                 131.575832
Benchmark Return [%]             -68.674573
Max Gross Exposure [%]            10.116275
Total Fees Paid                    0.000000
Max Drawdown [%]                   0.275003
Max Drawdown Duration           3155.000000
Total Trades                    6291.000000
Total Closed Trades             6291.000000
Total Open Trades                  0.000000
Open Trade PnL                     0.000000
Win Rate [%]                      57.939914
Best Trade [%]                     9.727687
Worst Trade [%]                   -2.907393
Avg Winning Trade [%]              0.466887
Avg Losing Trade [%]              -0.145953
Avg Winning Trade Duration        43.337174
Avg Losing Trade Duration         10.857467
Profit Factor                   

In [138]:
pd.set_option('display.max_rows', None)
trade_df = pf.trades.records_readable
# display(trade_df)
display(trade_df.sort_values(by='Return'))
# print(len(trade_df[trade_df['Return'] < 0]))
print(sum(trade_df['PnL']))

Exit Trade Id  Column      Size  Entry Timestamp  Avg Entry Price  \
5527           5527       0  0.004420           470009         22626.24   
3900           3900       0  0.003329           333179         30036.47   
1685           1685       0  0.002616           139229         38231.57   
5956           5956       0  0.005004           504539         19982.45   
1933           1933       0  0.002240           160439         44635.64   
3372           3372       0  0.003153           287609         31715.88   
4313           4313       0  0.005155           364919         19396.99   
3988           3988       0  0.004597           340799         21752.16   
5675           5675       0  0.005124           481919         19517.85   
2388           2388       0  0.002567           197999         38952.30   
3266           3266       0  0.002560           277139         39059.92   
6027           6027       0  0.005228           511769         19128.58   
4368           4368       0  0.004935           370169         20264.69   
2699           2699       0  0.002122           225959         47136.21   
5558           5558       0  0.004966           472559         20135.33   
4012           4012       0  0.004743           342239         21085.26   
2173           2173       0  0.002843           180119         35176.59   
3402           3402       0  0.003162           290159         31625.02   
3990           3990       0  0.004603           340889         21724.61   
3419           3419       0  0.003383           291719         29561.28   
3407           3407       0  0.003320           290759         30118.18   
3409           3409       0  0.003682           291149         27162.21   
5566           5566       0  0.005083           473069         19671.54   
3997           3997       0  0.004366           341189         22903.65   
4373           4373       0  0.004967           370619         20132.06   
3945           3945       0  0.003886           337109         25735.66   
3430           3430       0  0.003325           292319         30075.42   
3952           3952       0  0.004237           337619         23603.25   
5629           5629       0  0.005436           478319         18397.54   
2401           2401       0  0.002366           199079         42258.99   
2437           2437       0  0.002507           202139         39893.98   
1583           1583       0  0.002609           132119         38327.48   
3759           3759       0  0.003285           320519         30437.48   
3950           3950       0  0.004212           337499         23742.00   
5339           5339       0  0.004931           454199         20278.57   
595             595       0  0.001694            50069         59039.14   
3934           3934       0  0.003666           336209         27277.99   
4071           4071       0  0.004934           346619         20266.75   
568             568       0  0.001763            48149         56732.90   
5821           5821       0  0.005112           493319         19561.75   
1364           1364       0  0.002443           113309         40936.24   
749             749       0  0.002109            62579         47421.93   
3425           3425       0  0.003431           292109         29144.56   
1635           1635       0  0.002953           135869         33860.52   
4780           4780       0  0.004164           403979         24014.29   
4020           4020       0  0.004809           342659         20792.55   
5994           5994       0  0.005149           508589         19420.80   
2696           2696       0  0.002166           225719         46173.15   
1957           1957       0  0.002330           162299         42921.83   
1665           1665       0  0.002700           137879         37043.00   
4375           4375       0  0.004958           370739         20169.63   
4121           4121       0  0.004795           349679         20856.98   
3486           3486       0  0.

946.4434633771801
